In [1]:
import adaptive
adaptive.notebook_extension()

import asyncio
from functools import partial
import random

offset = random.uniform(-0.5, 0.5)

def f(x, offset=offset):
    a = 0.01
    return x + a**2 / (a**2 + (x - offset)**2)

In [2]:
# Let's create two learners and run only one.
learner = adaptive.Learner1D(f, bounds=(-1, 1))
control = adaptive.Learner1D(f, bounds=(-1, 1))

# Let's only run the learner
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01)

In [3]:
await runner.task  # This is not needed in a notebook environment!

In [4]:
runner.live_info()

In [5]:
fname = 'data/example_file.p'
learner.save(fname)
control.load(fname)

(learner.plot().relabel('saved learner')
 + control.plot().relabel('loaded learner'))

:Layout
   .Overlay.Saved_learner  :Overlay
      .Scatter.I :Scatter   [x]   (y)
   .Overlay.Loaded_learner :Overlay
      .Scatter.I :Scatter   [x]   (y)

In [6]:
control = adaptive.Learner1D(f, bounds=(-1, 1))
control.copy_from(learner)

In [7]:
def slow_f(x):
    from time import sleep
    sleep(5)
    return x

learner = adaptive.Learner1D(slow_f, bounds=[0, 1])
runner = adaptive.Runner(learner, goal=lambda l: l.npoints > 100)
runner.start_periodic_saving(save_kwargs=dict(fname='data/periodic_example.p'), interval=6)

<Task pending name='Task-5' coro=<AsyncRunner.start_periodic_saving.<locals>._saver() running at /home/docs/checkouts/readthedocs.org/user_builds/adaptive/checkouts/v0.12.2/adaptive/runner.py:682>>

In [8]:
await asyncio.sleep(6)  # This is not needed in a notebook environment!
runner.cancel()

In [9]:
runner.live_info()  # we cancelled it after 6 seconds

In [10]:
# See the data 6 later seconds with
!ls -lah data  # only works on macOS and Linux systems

total 16K
drwxr-xr-x 2 docs docs 4.0K Mar 23 22:06 .
drwxr-xr-x 8 docs docs 4.0K Mar 23 22:06 ..
-rw------- 1 docs docs 3.7K Mar 23 22:06 example_file.p
-rw------- 1 docs docs   38 Mar 23 22:06 periodic_example.p


In [11]:
learner = adaptive.Learner1D(f, bounds=(-1, 1))
adaptive.BlockingRunner(learner, goal=lambda l: l.loss() < 0.01)
# This will only get run after the runner has finished
learner.plot()

:Overlay
   .Scatter.I :Scatter   [x]   (y)

In [12]:
learner = adaptive.Learner1D(f, bounds=(-1, 1))

# blocks until completion
adaptive.runner.simple(learner, goal=lambda l: l.loss() < 0.01)

learner.plot()

:Overlay
   .Scatter.I :Scatter   [x]   (y)

In [13]:
from adaptive.runner import SequentialExecutor

learner = adaptive.Learner1D(f, bounds=(-1, 1))

runner = adaptive.Runner(learner, executor=SequentialExecutor(), goal=lambda l: l.loss() < 0.01)

In [14]:
await runner.task  # This is not needed in a notebook environment!

In [15]:
runner.live_info()

In [16]:
runner.live_plot(update_interval=0.1)

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I :Scatter   [x]   (y)

In [17]:
learner = adaptive.Learner1D(f, bounds=(-1, 1))
runner = adaptive.Runner(learner)

In [18]:
await asyncio.sleep(0.1)  # This is not needed in the notebook!

In [19]:
runner.cancel()  # Let's execute this after 0.1 seconds

In [20]:
runner.live_info()

In [21]:
runner.live_plot(update_interval=0.1)

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I :Scatter   [x]   (y)

In [22]:
print(runner.status())

cancelled


In [23]:
def will_raise(x):
    from random import random
    from time import sleep

    sleep(random())
    if random() < 0.1:
        raise RuntimeError('something went wrong!')
    return x**2

learner = adaptive.Learner1D(will_raise, (-1, 1))
runner = adaptive.Runner(learner)  # without 'goal' the runner will run forever unless cancelled

In [24]:
await asyncio.sleep(4)  # in 4 seconds it will surely have failed

In [25]:
runner.live_info()

In [26]:
runner.live_plot()

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Scatter.I :Scatter   [x]   (y)

In [27]:
runner.task.done()

True

In [28]:
runner.task.result()

RuntimeError: An error occured while evaluating "learner.function(0.875)". See the traceback for details.:

concurrent.futures.process._RemoteTraceback: 
"""
Traceback (most recent call last):
  File "/home/docs/checkouts/readthedocs.org/user_builds/adaptive/conda/v0.12.2/lib/python3.9/concurrent/futures/process.py", line 243, in _process_worker
    r = call_item.fn(*call_item.args, **call_item.kwargs)
  File "<ipython-input-23-029239453aff>", line 7, in will_raise
    raise RuntimeError('something went wrong!')
RuntimeError: something went wrong!
"""

The above exception was the direct cause of the following exception:

Traceback (most recent call last):
  File "/home/docs/checkouts/readthedocs.org/user_builds/adaptive/checkouts/v0.12.2/adaptive/runner.py", line 217, in _process_futures
    y = fut.result()
RuntimeError: something went wrong!


In [29]:
for point, tb in runner.tracebacks:
    print(f'point: {point}:\n {tb}')

point: 0.875:
 concurrent.futures.process._RemoteTraceback: 
"""
Traceback (most recent call last):
  File "/home/docs/checkouts/readthedocs.org/user_builds/adaptive/conda/v0.12.2/lib/python3.9/concurrent/futures/process.py", line 243, in _process_worker
    r = call_item.fn(*call_item.args, **call_item.kwargs)
  File "<ipython-input-23-029239453aff>", line 7, in will_raise
    raise RuntimeError('something went wrong!')
RuntimeError: something went wrong!
"""

The above exception was the direct cause of the following exception:

Traceback (most recent call last):
  File "/home/docs/checkouts/readthedocs.org/user_builds/adaptive/checkouts/v0.12.2/adaptive/runner.py", line 217, in _process_futures
    y = fut.result()
RuntimeError: something went wrong!



In [30]:
learner = adaptive.Learner1D(f, bounds=(-1, 1))
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01,
                         log=True)

In [31]:
await runner.task  # This is not needed in a notebook environment!

In [32]:
runner.live_info()

In [33]:
reconstructed_learner = adaptive.Learner1D(f, bounds=learner.bounds)
adaptive.runner.replay_log(reconstructed_learner, runner.log)

In [34]:
learner.plot().Scatter.I.opts(style=dict(size=6)) * reconstructed_learner.plot()

:Overlay
   .Scatter.I  :Scatter   [x]   (y)
   .Scatter.II :Scatter   [x]   (y)

In [35]:
import asyncio

async def time(runner):
    from datetime import datetime
    now = datetime.now()
    await runner.task
    return datetime.now() - now

ioloop = asyncio.get_event_loop()

learner = adaptive.Learner1D(f, bounds=(-1, 1))
runner = adaptive.Runner(learner, goal=lambda l: l.loss() < 0.01)

timer = ioloop.create_task(time(runner))

In [36]:
await runner.task  # This is not needed in a notebook environment!

In [37]:
# The result will only be set when the runner is done.
timer.result()

datetime.timedelta(microseconds=243388)